In [1]:
import pandas as pd
type = "summary_50"

type_train_df_x = pd.read_parquet(f"df/{type}_train_df_x.gzip")
type_test_df_x = pd.read_parquet(f"df/{type}_test_df_x.gzip")

type_train_df_y = pd.read_parquet(f"df/{type}_train_df_y.gzip")
type_test_df_y = pd.read_parquet(f"df/{type}_test_df_y.gzip")
joined_train_df = pd.concat([type_train_df_x, type_train_df_y], axis=1).reset_index(drop=True)
joined_test_df = pd.concat([type_test_df_x, type_test_df_y], axis=1).reset_index(drop=True)

joined = pd.concat([joined_train_df, joined_test_df], axis=0).reset_index(drop=True)
joined = joined.drop('id', axis=1)

In [59]:
import time
import numpy as np
import pandas as pd
from sklearn.preprocessing import LabelBinarizer
from econml.dml import CausalForestDML
from sklearn.linear_model import LogisticRegression
import dowhy
from dowhy import CausalModel

def calculate_mediation_dowhy(
    treatment_col: str,
    mediator_col: str,
    outcome_col: str = "int_bias",
    common_causes: list[str] | None = None,
    effect_modifiers: list[str] | None = None,
    df: pd.DataFrame = joined,
    verbose: bool = True
):
    """
    For each outcome class (from a multi-class Y), fit a DoWhy mediation analysis
    with CausalForestDML as the underlying estimator.  Returns direct, indirect, and
    total effects (both point estimates and heterogeneous arrays) per class.
    
    Args:
        treatment_col:   name of the T column (e.g. "sentimentPolitics")
        mediator_col:    name of the M column (e.g. "sentimentDonaldTrump")
        outcome_col:     name of the multi-class outcome (must be integer labels)
        common_causes:   list of confounder column names (topics + other controls)
        effect_modifiers: list of columns to pass as X for heterogeneity
        df:              the full DataFrame (must contain all columns)
        verbose:         whether to print progress
    
    Returns:
        direct_h        dict[class -> np.ndarray]  heterogeneous NDE per row of X  
        indirect_h      dict[class -> np.ndarray]  heterogeneous NIE per row of X  
        total_h         dict[class -> np.ndarray]  heterogeneous total effect per row of X  
        direct_avg      dict[class -> float]       average NDE  
        indirect_avg    dict[class -> float]       average NIE  
        total_avg       dict[class -> float]       average total effect  
        models          dict[class -> dowhy.MediationEstimate]  the DoWhy result objects
    """
    start = time.time()
    # 1) subset to rows where the treatment topic is active
    primary_topic = treatment_col.replace("sentiment", "topic")
    secondary_topic = mediator_col.replace("sentiment", "topic")
    df_sub = df[(df[primary_topic] == True) & (df[secondary_topic] == True)].reset_index(drop=True)
    if verbose:
        print(f"Using {len(df_sub)} rows where {primary_topic}=True and {secondary_topic}=True")

    # 2) prepare T, M, Y, W, X
    T = df_sub[treatment_col].astype(int)
    M = df_sub[mediator_col].astype(int)
    lb      = LabelBinarizer()
    Y_multi = lb.fit_transform(df_sub[outcome_col])
    classes = lb.classes_

    # default confounders: everything except T, M, outcome, modifiers
    if common_causes is None:
        common_causes = [c for c in df_sub.columns
                         if c not in {treatment_col, mediator_col, outcome_col}
                         and not c.startswith("sentiment")]
    # default effect modifiers = all other sentiment columns
    if effect_modifiers is None:
        effect_modifiers = [c for c in df_sub.columns
                            if c.startswith("sentiment") and c != treatment_col]

    direct_h, indirect_h, total_h = {}, {}, {}
    direct_avg, indirect_avg, total_avg = {}, {}, {}
    models = {}

    nie_dict = {}
    nde_dict = {}

    for i, cls in enumerate(classes):
        nie_dict[cls] = {}
        nde_dict[cls] = {}
        y = Y_multi[:, i]
        # skip tiny classes
        if np.bincount(y).min() < 5:
            if verbose:
                print(f"Skipping class {cls} (too few positives/negatives).")
            continue
        if verbose:
            print(f"Estimating mediation for class {cls}...")

        # 3) build the DoWhy causal graph + model
        data = pd.concat([
            T.rename("T"),
            M.rename("M"),
            pd.Series(y, name="Y"),
            df_sub[common_causes],
            df_sub[effect_modifiers]
        ], axis=1)
        # simple graph string: T->M->Y and T->Y plus confounders into both
        graph = """
        digraph {
            U[label="unobserved"];
            "T" -> "M";
            "M" -> "Y";
            "T" -> "Y";
        }
        """
        model = CausalModel(
            data=data,
            treatment="T",
            outcome="Y",
            common_causes=common_causes,
            effect_modifiers=effect_modifiers,
            graph=graph
        )

        identified_estimand_nie = model.identify_effect(proceed_when_unidentifiable=True, estimand_type="nonparametric-nie")
        identified_estimand_nde = model.identify_effect(proceed_when_unidentifiable=True, estimand_type="nonparametric-nde")

        effects = [(0, 1), (0, -1), (-1, 1)]

        for c, t in effects:
            nie = model.estimate_effect(identified_estimand_nie,
                    method_name="mediation.two_stage_regression",
                    confidence_intervals=False,
                    test_significance=False,
                    method_params = {
                        'first_stage_model': dowhy.causal_estimators.linear_regression_estimator.LinearRegressionEstimator,
                        'second_stage_model': dowhy.causal_estimators.linear_regression_estimator.LinearRegressionEstimator
                    },
                    control_value=c,
                    treatment_value=t
            )
            nde = model.estimate_effect(identified_estimand_nde,
                    method_name="mediation.two_stage_regression",
                    confidence_intervals=False,
                    test_significance=False,
                    method_params = {
                        'first_stage_model': dowhy.causal_estimators.linear_regression_estimator.LinearRegressionEstimator,
                        'second_stage_model': dowhy.causal_estimators.linear_regression_estimator.LinearRegressionEstimator
                    },
                    control_value=c,
                    treatment_value=t
            )
            nie_dict[cls][f"{c} vs {t}"] = nie
            nde_dict[cls][f"{c} vs {t}"] = nde

    if verbose:
        print(f"Done in {time.time()-start:.1f}s")

    return (nie_dict, nde_dict)


In [60]:
nie, nde = calculate_mediation_dowhy(
    treatment_col = 'sentiment Politics',
    mediator_col = 'sentiment Donald Trump',
    common_causes = [c for c in joined.columns if not c.startswith("sentiment") and c != 'int_bias'],
    effect_modifiers = [c for c in joined.columns if c.startswith("sentiment") and c != 'sentiment Politics' and c != 'sentiment Donald Trump'],
    df = joined
)

Using 1620 rows where topic Politics=True and topic Donald Trump=True
Estimating mediation for class 0...
two_stage_regression
{'control_value': 0, 'treatment_value': 1, 'test_significance': False, 'evaluate_effect_strength': False, 'confidence_intervals': False, 'target_units': 'ate', 'effect_modifiers': ['sentiment  Donald Trump', 'sentiment 14th Amendment', 'sentiment 1619 Project', 'sentiment 1st Amendment', 'sentiment 2002 Elections', 'sentiment 2016 Election', 'sentiment 2020 Census', 'sentiment 2020 Election', 'sentiment 2020 Election Fact Checking', 'sentiment 2022 Arizona Senate Election', 'sentiment 2022 Elections', 'sentiment 2022 Florida Gubernatorial Election', 'sentiment 2022 Florida Senate Election', 'sentiment 2022 Georgia Gubernatorial Election', 'sentiment 2022 Georgia Senate Election', 'sentiment 2022 Gubernatorial Races', 'sentiment 2022 Massachusetts Gubernatorial Election', 'sentiment 2022 Nevada Senate Election', 'sentiment 2022 Ohio Senate Election', 'sentiment 

The default of observed=False is deprecated and will be changed to True in a future version of pandas. Pass observed=False to retain current behavior or observed=True to adopt the future default and silence this warning.
Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`


{'control_value': 0, 'treatment_value': 1, 'test_significance': False, 'evaluate_effect_strength': False, 'confidence_intervals': False, 'target_units': 'ate', 'effect_modifiers': ['sentiment  Donald Trump', 'sentiment 14th Amendment', 'sentiment 1619 Project', 'sentiment 1st Amendment', 'sentiment 2002 Elections', 'sentiment 2016 Election', 'sentiment 2020 Census', 'sentiment 2020 Election', 'sentiment 2020 Election Fact Checking', 'sentiment 2022 Arizona Senate Election', 'sentiment 2022 Elections', 'sentiment 2022 Florida Gubernatorial Election', 'sentiment 2022 Florida Senate Election', 'sentiment 2022 Georgia Gubernatorial Election', 'sentiment 2022 Georgia Senate Election', 'sentiment 2022 Gubernatorial Races', 'sentiment 2022 Massachusetts Gubernatorial Election', 'sentiment 2022 Nevada Senate Election', 'sentiment 2022 Ohio Senate Election', 'sentiment 2022 Pennsylvania Senate Election', 'sentiment 2022 Texas Attorney General Election', 'sentiment 2022 Texas Gubernatorial Elect

The default of observed=False is deprecated and will be changed to True in a future version of pandas. Pass observed=False to retain current behavior or observed=True to adopt the future default and silence this warning.
Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`


two_stage_regression
{'control_value': 0, 'treatment_value': 1, 'test_significance': False, 'evaluate_effect_strength': False, 'confidence_intervals': False, 'target_units': 'ate', 'effect_modifiers': ['sentiment  Donald Trump', 'sentiment 14th Amendment', 'sentiment 1619 Project', 'sentiment 1st Amendment', 'sentiment 2002 Elections', 'sentiment 2016 Election', 'sentiment 2020 Census', 'sentiment 2020 Election', 'sentiment 2020 Election Fact Checking', 'sentiment 2022 Arizona Senate Election', 'sentiment 2022 Elections', 'sentiment 2022 Florida Gubernatorial Election', 'sentiment 2022 Florida Senate Election', 'sentiment 2022 Georgia Gubernatorial Election', 'sentiment 2022 Georgia Senate Election', 'sentiment 2022 Gubernatorial Races', 'sentiment 2022 Massachusetts Gubernatorial Election', 'sentiment 2022 Nevada Senate Election', 'sentiment 2022 Ohio Senate Election', 'sentiment 2022 Pennsylvania Senate Election', 'sentiment 2022 Texas Attorney General Election', 'sentiment 2022 Texa

...

The default of observed=False is deprecated and will be changed to True in a future version of pandas. Pass observed=False to retain current behavior or observed=True to adopt the future default and silence this warning.
Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`


{'control_value': -1, 'treatment_value': 1, 'test_significance': False, 'evaluate_effect_strength': False, 'confidence_intervals': False, 'target_units': 'ate', 'effect_modifiers': ['sentiment  Donald Trump', 'sentiment 14th Amendment', 'sentiment 1619 Project', 'sentiment 1st Amendment', 'sentiment 2002 Elections', 'sentiment 2016 Election', 'sentiment 2020 Census', 'sentiment 2020 Election', 'sentiment 2020 Election Fact Checking', 'sentiment 2022 Arizona Senate Election', 'sentiment 2022 Elections', 'sentiment 2022 Florida Gubernatorial Election', 'sentiment 2022 Florida Senate Election', 'sentiment 2022 Georgia Gubernatorial Election', 'sentiment 2022 Georgia Senate Election', 'sentiment 2022 Gubernatorial Races', 'sentiment 2022 Massachusetts Gubernatorial Election', 'sentiment 2022 Nevada Senate Election', 'sentiment 2022 Ohio Senate Election', 'sentiment 2022 Pennsylvania Senate Election', 'sentiment 2022 Texas Attorney General Election', 'sentiment 2022 Texas Gubernatorial Elec

The default of observed=False is deprecated and will be changed to True in a future version of pandas. Pass observed=False to retain current behavior or observed=True to adopt the future default and silence this warning.


Done in 12914.2s


Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`


In [67]:
import pandas as pd
type = "summary_100"

type_train_df_x = pd.read_parquet(f"df/{type}_train_df_x.gzip")
type_test_df_x = pd.read_parquet(f"df/{type}_test_df_x.gzip")

type_train_df_y = pd.read_parquet(f"df/{type}_train_df_y.gzip")
type_test_df_y = pd.read_parquet(f"df/{type}_test_df_y.gzip")
joined_train_df = pd.concat([type_train_df_x, type_train_df_y], axis=1).reset_index(drop=True)
joined_test_df = pd.concat([type_test_df_x, type_test_df_y], axis=1).reset_index(drop=True)

joined2 = pd.concat([joined_train_df, joined_test_df], axis=0).reset_index(drop=True)
joined2 = joined2.drop('id', axis=1)

In [69]:
nie100, nde100 = calculate_mediation_dowhy(
    treatment_col = 'sentiment Politics',
    mediator_col = 'sentiment Donald Trump',
    common_causes = [c for c in joined2.columns if not c.startswith("sentiment") and c != 'int_bias'],
    effect_modifiers = [c for c in joined2.columns if c.startswith("sentiment") and c != 'sentiment Politics' and c != 'sentiment Donald Trump'],
    df = joined2
)

Using 1676 rows where topic Politics=True and topic Donald Trump=True
Estimating mediation for class 0...
two_stage_regression
{'control_value': 0, 'treatment_value': 1, 'test_significance': False, 'evaluate_effect_strength': False, 'confidence_intervals': False, 'target_units': 'ate', 'effect_modifiers': ['sentiment  Defense And Security', 'sentiment  Democratic Party', 'sentiment  FOREIGN POLICY', 'sentiment  Politics', 'sentiment 14th Amendment', 'sentiment 1619 Project', 'sentiment 1st Amendment', 'sentiment 2012', 'sentiment 2014', 'sentiment 2016 Election', 'sentiment 2020 Census', 'sentiment 2020 Election', 'sentiment 2020 Election Fact Checking', 'sentiment 2022 Arizona Senate Election', 'sentiment 2022 Elections', 'sentiment 2022 Florida Gubernatorial Election', 'sentiment 2022 Florida Senate Election', 'sentiment 2022 Georgia Gubernatorial Election', 'sentiment 2022 Georgia Senate Election', 'sentiment 2022 Gubernatorial Races', 'sentiment 2022 Massachusetts Gubernatorial Ele

The default of observed=False is deprecated and will be changed to True in a future version of pandas. Pass observed=False to retain current behavior or observed=True to adopt the future default and silence this warning.
Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`


{'control_value': 0, 'treatment_value': 1, 'test_significance': False, 'evaluate_effect_strength': False, 'confidence_intervals': False, 'target_units': 'ate', 'effect_modifiers': ['sentiment  Defense And Security', 'sentiment  Democratic Party', 'sentiment  FOREIGN POLICY', 'sentiment  Politics', 'sentiment 14th Amendment', 'sentiment 1619 Project', 'sentiment 1st Amendment', 'sentiment 2012', 'sentiment 2014', 'sentiment 2016 Election', 'sentiment 2020 Census', 'sentiment 2020 Election', 'sentiment 2020 Election Fact Checking', 'sentiment 2022 Arizona Senate Election', 'sentiment 2022 Elections', 'sentiment 2022 Florida Gubernatorial Election', 'sentiment 2022 Florida Senate Election', 'sentiment 2022 Georgia Gubernatorial Election', 'sentiment 2022 Georgia Senate Election', 'sentiment 2022 Gubernatorial Races', 'sentiment 2022 Massachusetts Gubernatorial Election', 'sentiment 2022 Nevada Senate Election', 'sentiment 2022 Ohio Senate Election', 'sentiment 2022 Pennsylvania Senate Ele

The default of observed=False is deprecated and will be changed to True in a future version of pandas. Pass observed=False to retain current behavior or observed=True to adopt the future default and silence this warning.
Exception ignored in: <bound method IPythonKernel._clean_thread_parent_frames of <ipykernel.ipkernel.IPythonKernel object at 0x104957200>>
Traceback (most recent call last):
  File "/Users/upasana/code/playground/ci2_proj/.venv/lib/python3.12/site-packages/ipykernel/ipkernel.py", line 775, in _clean_thread_parent_frames
    def _clean_thread_parent_frames(

KeyboardInterrupt: 
Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`


two_stage_regression
{'control_value': 0, 'treatment_value': 1, 'test_significance': False, 'evaluate_effect_strength': False, 'confidence_intervals': False, 'target_units': 'ate', 'effect_modifiers': ['sentiment  Defense And Security', 'sentiment  Democratic Party', 'sentiment  FOREIGN POLICY', 'sentiment  Politics', 'sentiment 14th Amendment', 'sentiment 1619 Project', 'sentiment 1st Amendment', 'sentiment 2012', 'sentiment 2014', 'sentiment 2016 Election', 'sentiment 2020 Census', 'sentiment 2020 Election', 'sentiment 2020 Election Fact Checking', 'sentiment 2022 Arizona Senate Election', 'sentiment 2022 Elections', 'sentiment 2022 Florida Gubernatorial Election', 'sentiment 2022 Florida Senate Election', 'sentiment 2022 Georgia Gubernatorial Election', 'sentiment 2022 Georgia Senate Election', 'sentiment 2022 Gubernatorial Races', 'sentiment 2022 Massachusetts Gubernatorial Election', 'sentiment 2022 Nevada Senate Election', 'sentiment 2022 Ohio Senate Election', 'sentiment 2022 Pe

...

The default of observed=False is deprecated and will be changed to True in a future version of pandas. Pass observed=False to retain current behavior or observed=True to adopt the future default and silence this warning.
Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`


{'control_value': -1, 'treatment_value': 1, 'test_significance': False, 'evaluate_effect_strength': False, 'confidence_intervals': False, 'target_units': 'ate', 'effect_modifiers': ['sentiment  Defense And Security', 'sentiment  Democratic Party', 'sentiment  FOREIGN POLICY', 'sentiment  Politics', 'sentiment 14th Amendment', 'sentiment 1619 Project', 'sentiment 1st Amendment', 'sentiment 2012', 'sentiment 2014', 'sentiment 2016 Election', 'sentiment 2020 Census', 'sentiment 2020 Election', 'sentiment 2020 Election Fact Checking', 'sentiment 2022 Arizona Senate Election', 'sentiment 2022 Elections', 'sentiment 2022 Florida Gubernatorial Election', 'sentiment 2022 Florida Senate Election', 'sentiment 2022 Georgia Gubernatorial Election', 'sentiment 2022 Georgia Senate Election', 'sentiment 2022 Gubernatorial Races', 'sentiment 2022 Massachusetts Gubernatorial Election', 'sentiment 2022 Nevada Senate Election', 'sentiment 2022 Ohio Senate Election', 'sentiment 2022 Pennsylvania Senate El

The default of observed=False is deprecated and will be changed to True in a future version of pandas. Pass observed=False to retain current behavior or observed=True to adopt the future default and silence this warning.


Done in 13144.1s


Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`


In [ ]:
import pandas as pd
type = "text"

type_train_df_x = pd.read_parquet(f"df/{type}_train_df_x.gzip")
type_test_df_x = pd.read_parquet(f"df/{type}_test_df_x.gzip")

type_train_df_y = pd.read_parquet(f"df/{type}_train_df_y.gzip")
type_test_df_y = pd.read_parquet(f"df/{type}_test_df_y.gzip")
joined_train_df = pd.concat([type_train_df_x, type_train_df_y], axis=1).reset_index(drop=True)
joined_test_df = pd.concat([type_test_df_x, type_test_df_y], axis=1).reset_index(drop=True)

joined3 = pd.concat([joined_train_df, joined_test_df], axis=0).reset_index(drop=True)
joined3 = joined3.drop('id', axis=1)

nietext, ndetext = calculate_mediation_dowhy(
    treatment_col = 'sentiment Politics',
    mediator_col = 'sentiment Donald Trump',
    common_causes = [c for c in joined3.columns if not c.startswith("sentiment") and c != 'int_bias'],
    effect_modifiers = [c for c in joined3.columns if c.startswith("sentiment") and c != 'sentiment Politics' and c != 'sentiment Donald Trump'],
    df = joined3
)

In [70]:
import joblib


dct = {
    "nie50": nie,
    "nde50": nde,
    "nie100": nie100,
    "nde100": nde100,
    # "nietext": nietext,
    # "ndetext": ndetext
}

joblib.dump(dct, "nie_nde.pkl")

['nie_nde.pkl']